# ETL (Part 1) Loading the survey raw data into a database using SQLite

In [61]:
# Import dependencies
import pandas as pd
import sqlite3
from tabulate import tabulate

In [62]:
# Define the path to the CSV file
survey_raw_data = 'data/survey.csv'

In [63]:
# Load the CSV data into a DataFrame
survey_raw_df = pd.read_csv(survey_raw_data)

## Cleanup the columns

### Clean up column[Gender]

In [64]:
survey_raw_df['Gender'] = survey_raw_df['Gender'].str.strip()
survey_raw_df['Gender'] = survey_raw_df['Gender'].str.lower()

male_variations = ['male', 'm', 'maile', 'cis male', 'mal', 'male (cis)', 'make', 'man', 'msle', 'mail', 'malr', 'cis man']
female_variations = ['female', 'f', 'cis female', 'woman', 'femake', 'female (cis)', 'femail']

for male_variation in male_variations:
    survey_raw_df['Gender'] = survey_raw_df['Gender'].replace(male_variation, 'M')

for female_variation in female_variations:
    survey_raw_df['Gender'] = survey_raw_df['Gender'].replace(female_variation, 'F')


### Determine remaining values in Gender column

In [65]:
remaining = survey_raw_df[survey_raw_df['Gender'] != 'M']
remaining = remaining[remaining['Gender'] != 'F']

print(remaining['Gender'].count())
remaining.head(50)

14


Timestamp  Age        Gender         Country state  \
72    2014-08-27 11:54:27   23  trans-female   United States    MA   
306   2014-08-27 14:22:36   30         queer   United States    IL   
349   2014-08-27 14:47:28   25    non-binary   United States    CA   
387   2014-08-27 15:24:22   29    non-binary   United States    CA   
412   2014-08-27 15:30:51   31    non-binary  United Kingdom   NaN   
415   2014-08-27 15:31:20   30    non-binary         Germany   NaN   
450   2014-08-27 15:53:59   40         queer   United States    VA   
543   2014-08-27 18:13:38   28    non-binary  United Kingdom   NaN   
552   2014-08-27 18:56:46   21    non-binary  United Kingdom   NaN   
681   2014-08-28 09:02:16   19  trans-female   United States    MO   
776   2014-08-28 12:10:08   32    non-binary  United Kingdom   NaN   
804   2014-08-28 13:47:57   28  trans-female   United States    CA   
817   2014-08-28 14:46:08   26         queer         Germany   NaN   
1015  2014-08-29 09:58:55   46  trans-female   United States    CT   

     self_employed family_history treatment work_interfere    no_employees  \
72              No             No        No         Rarely  More than 1000   
306             No            Yes       Yes         Rarely          26-100   
349             No            Yes       Yes      Sometimes  More than 1000   
387            Yes            Yes       Yes      Sometimes             1-5   
412             No            Yes       Yes      Sometimes  More than 1000   
415             No            Yes       Yes      Sometimes         100-500   
450             No            Yes        No          Never  More than 1000   
543             No            Yes       Yes         Rarely         100-500   
552             No             No       Yes      Sometimes          26-100   
681             No            Yes       Yes          Often          26-100   
776             No             No       Yes      Sometimes  More than 1000   
804             No             No       Yes      Sometimes          26-100   
817            Yes             No       Yes      Sometimes            6-25   
1015            No             No       Yes          Often  More than 1000   

      ...               leave mental_health_consequence  \
72    ...  Somewhat difficult                     Maybe   
306   ...       Somewhat easy                     Maybe   
349   ...          Don't know                     Maybe   
387   ...      Very difficult                       Yes   
412   ...          Don't know                       Yes   
415   ...  Somewhat difficult                        No   
450   ...          Don't know                       Yes   
543   ...  Somewhat difficult                       Yes   
552   ...       Somewhat easy                     Maybe   
681   ...  Somewhat difficult                     Maybe   
776   ...          Don't know                        No   
804   ...  Somewhat difficult                       Yes   
817   ...           Very easy                        No   
1015  ...          Don't know                       Yes   

     phys_health_consequence     coworkers    supervisor  \
72                        No           Yes           Yes   
306                       No  Some of them           Yes   
349                       No  Some of them  Some of them   
387                       No  Some of them            No   
412                    Maybe            No            No   
415                       No           Yes           Yes   
450                    Maybe            No  Some of them   
543                      Yes  Some of them  Some of them   
552                       No  Some of them  Some of them   
681                    Maybe            No            No   
776                       No           Yes  Some of them   
804                    Maybe  Some of them  Some of them   
817                       No  Some of them  Some of them   
1015                      No  Some of them  Some of them   

     me

### Abbreviate genders

In [66]:
gender_abbreviations = {
    "trans-female"  : "TF",
    "trans-male"    : "TM",
    "queer"         : "Q",
    "non-binary"    : "NB"
}

for gender_name, gender_abbreviation in gender_abbreviations.items():
    survey_raw_df['Gender'] = survey_raw_df['Gender'].replace(gender_name, gender_abbreviation)

survey_raw_df.head()


Timestamp  Age Gender         Country state self_employed  \
0  2014-08-27 11:29:31   37      F   United States    IL           NaN   
1  2014-08-27 11:29:37   44      M   United States    IN           NaN   
2  2014-08-27 11:29:44   32      M          Canada   NaN           NaN   
3  2014-08-27 11:29:46   31      M  United Kingdom   NaN           NaN   
4  2014-08-27 11:30:22   31      M   United States    TX           NaN   

  family_history treatment work_interfere    no_employees  ...  \
0             No       Yes          Often            6-25  ...   
1             No        No         Rarely  More than 1000  ...   
2             No        No         Rarely            6-25  ...   
3            Yes       Yes          Often          26-100  ...   
4             No        No          Never         100-500  ...   

                leave mental_health_consequence phys_health_consequence  \
0       Somewhat easy                        No                      No   
1          Don't know                     Maybe                      No   
2  Somewhat difficult                        No                      No   
3  Somewhat difficult                       Yes                     Yes   
4          Don't know                        No                      No   

      coworkers supervisor mental_health_interview phys_health_interview  \
0  Some of them        Yes                      No                 Maybe   
1            No         No                      No                    No   
2           Yes        Yes                     Yes                   Yes   
3  Some of them         No                   Maybe                 Maybe   
4  Some of them        Yes                     Yes                   Yes   

  mental_vs_physical obs_consequence comments  
0                Yes              No      NaN  
1         Don't know              No      NaN  
2                 No              No      NaN  
3                 No             Yes      NaN  
4         Don't know              No      NaN  

[5 rows x 27 columns]

### Verify data in Gender columns are correctly abbreviated

In [67]:
remaining = survey_raw_df[survey_raw_df['Gender'] != 'M']
remaining = remaining[remaining['Gender'] != 'F']

print(remaining['Gender'].count())
remaining.head(20)

14


Timestamp  Age Gender         Country state self_employed  \
72    2014-08-27 11:54:27   23     TF   United States    MA            No   
306   2014-08-27 14:22:36   30      Q   United States    IL            No   
349   2014-08-27 14:47:28   25     NB   United States    CA            No   
387   2014-08-27 15:24:22   29     NB   United States    CA           Yes   
412   2014-08-27 15:30:51   31     NB  United Kingdom   NaN            No   
415   2014-08-27 15:31:20   30     NB         Germany   NaN            No   
450   2014-08-27 15:53:59   40      Q   United States    VA            No   
543   2014-08-27 18:13:38   28     NB  United Kingdom   NaN            No   
552   2014-08-27 18:56:46   21     NB  United Kingdom   NaN            No   
681   2014-08-28 09:02:16   19     TF   United States    MO            No   
776   2014-08-28 12:10:08   32     NB  United Kingdom   NaN            No   
804   2014-08-28 13:47:57   28     TF   United States    CA            No   
817   2014-08-28 14:46:08   26      Q         Germany   NaN           Yes   
1015  2014-08-29 09:58:55   46     TF   United States    CT            No   

     family_history treatment work_interfere    no_employees  ...  \
72               No        No         Rarely  More than 1000  ...   
306             Yes       Yes         Rarely          26-100  ...   
349             Yes       Yes      Sometimes  More than 1000  ...   
387             Yes       Yes      Sometimes             1-5  ...   
412             Yes       Yes      Sometimes  More than 1000  ...   
415             Yes       Yes      Sometimes         100-500  ...   
450             Yes        No          Never  More than 1000  ...   
543             Yes       Yes         Rarely         100-500  ...   
552              No       Yes      Sometimes          26-100  ...   
681             Yes       Yes          Often          26-100  ...   
776              No       Yes      Sometimes  More than 1000  ...   
804              No       Yes      Sometimes          26-100  ...   
817              No       Yes      Sometimes            6-25  ...   
1015             No       Yes          Often  More than 1000  ...   

                   leave mental_health_consequence phys_health_consequence  \
72    Somewhat difficult                     Maybe                      No   
306        Somewhat easy                     Maybe                      No   
349           Don't know                     Maybe                      No   
387       Very difficult                       Yes                      No   
412           Don't know                       Yes                   Maybe   
415   Somewhat difficult                        No                      No   
450           Don't know                       Yes                   Maybe   
543   Somewhat difficult                       Yes                     Yes   
552        Somewhat easy                     Maybe                      No   
681   Somewhat difficult                     Maybe                   Maybe   
776           Don't know                        No                      No   
804   Somewhat difficult                       Yes                   Maybe   
817            Very easy                        No                      No   
1015          Don't know                       Yes                      No   

         coworkers    supervisor mental_health_interview  \
72             Yes           Yes                      No   
306   Some of them           Yes                      No   
349   Some of them  Some of them                      No   
387   Some of them            No                      No   
412             No            No                      No   
415            Yes           Yes                   Maybe   
450             No  Some of them                      No   
543   Some of them  Some of them                     Yes   
552   Some of them  Some of them                      No   
681             No            No                     

### Filter Column['Age']

In [68]:
min_age = 0
max_age = 120
survey_raw_df = survey_raw_df[(survey_raw_df['Age'] >= min_age) & (survey_raw_df['Age'] <= max_age)]

### Clean up timestamp
1. Rename Timestamp to survey_date
2. Remove time - just keep date

In [69]:
survey_raw_df = survey_raw_df.rename(columns={'Timestamp': 'survey_date'})
survey_raw_df['survey_date'] = pd.to_datetime(survey_raw_df['survey_date']).dt.date
survey_raw_df.head()

survey_date  Age Gender         Country state self_employed family_history  \
0  2014-08-27   37      F   United States    IL           NaN             No   
1  2014-08-27   44      M   United States    IN           NaN             No   
2  2014-08-27   32      M          Canada   NaN           NaN             No   
3  2014-08-27   31      M  United Kingdom   NaN           NaN            Yes   
4  2014-08-27   31      M   United States    TX           NaN             No   

  treatment work_interfere    no_employees  ...               leave  \
0       Yes          Often            6-25  ...       Somewhat easy   
1        No         Rarely  More than 1000  ...          Don't know   
2        No         Rarely            6-25  ...  Somewhat difficult   
3       Yes          Often          26-100  ...  Somewhat difficult   
4        No          Never         100-500  ...          Don't know   

  mental_health_consequence phys_health_consequence     coworkers supervisor  \
0                        No                      No  Some of them        Yes   
1                     Maybe                      No            No         No   
2                        No                      No           Yes        Yes   
3                       Yes                     Yes  Some of them         No   
4                        No                      No  Some of them        Yes   

  mental_health_interview phys_health_interview mental_vs_physical  \
0                      No                 Maybe                Yes   
1                      No                    No         Don't know   
2                     Yes                   Yes                 No   
3                   Maybe                 Maybe                 No   
4                     Yes                   Yes         Don't know   

  obs_consequence comments  
0              No      NaN  
1              No      NaN  
2              No      NaN  
3             Yes      NaN  
4              No      NaN  

[5 rows x 27 columns]

### Create company size column

In [70]:
survey_raw_df['company_size'] = survey_raw_df['no_employees']
size_names = {
    "1-5"               : "Very Small",
    "6-25"              : "Small",
    "26-100"            : "Medium",
    "100-500"           : "Large",
    "500-1000"          : "Very Large",
    "More than 1000"    : "Mega"
}

for no_of_employees, size_name in size_names.items():
    survey_raw_df['company_size'] = survey_raw_df['company_size'].replace(no_of_employees, size_name)

survey_raw_df.head()

survey_date  Age Gender         Country state self_employed family_history  \
0  2014-08-27   37      F   United States    IL           NaN             No   
1  2014-08-27   44      M   United States    IN           NaN             No   
2  2014-08-27   32      M          Canada   NaN           NaN             No   
3  2014-08-27   31      M  United Kingdom   NaN           NaN            Yes   
4  2014-08-27   31      M   United States    TX           NaN             No   

  treatment work_interfere    no_employees  ... mental_health_consequence  \
0       Yes          Often            6-25  ...                        No   
1        No         Rarely  More than 1000  ...                     Maybe   
2        No         Rarely            6-25  ...                        No   
3       Yes          Often          26-100  ...                       Yes   
4        No          Never         100-500  ...                        No   

  phys_health_consequence     coworkers supervisor mental_health_interview  \
0                      No  Some of them        Yes                      No   
1                      No            No         No                      No   
2                      No           Yes        Yes                     Yes   
3                     Yes  Some of them         No                   Maybe   
4                      No  Some of them        Yes                     Yes   

  phys_health_interview mental_vs_physical obs_consequence comments  \
0                 Maybe                Yes              No      NaN   
1                    No         Don't know              No      NaN   
2                   Yes                 No              No      NaN   
3                 Maybe                 No             Yes      NaN   
4                   Yes         Don't know              No      NaN   

  company_size  
0        Small  
1         Mega  
2        Small  
3       Medium  
4        Large  

[5 rows x 28 columns]

## Write to the Database

### Create connection to SQLITE database

In [71]:
# Create a connection to the SQLite database
conn = sqlite3.connect('survey_database.db')
cursor = conn.cursor()

In [72]:
# Define the table name
table_name = "survey_raw_data"

In [73]:
# Create the table in SQLite (replace it if it already exists)
survey_raw_df.to_sql(table_name, conn, if_exists='replace', index=False)

1253

In [74]:
# Commit the changes
conn.commit()

In [75]:
# Verify that the data was loaded by querying the table
query = f"SELECT * FROM {table_name}"
result = pd.read_sql_query(query, conn)

In [76]:
# Close the connection
conn.close()

In [77]:
print(tabulate(result, headers='keys', tablefmt='psql'))

+------+---------------+-------+----------+------------------------+---------+-----------------+------------------+-------------+------------------+----------------+---------------+----------------+------------+----------------+--------------------+-------------+-------------+--------------------+-----------------------------+---------------------------+--------------+--------------+---------------------------+-------------------------+----------------------+-------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

# ETL (Part 2) Data Transformation

In [78]:
# Define the path to the SQLite database
db_path = 'survey_database.db'

# Create a connection to the SQLite database
conn = sqlite3.connect(db_path)